In [1]:
# !pip install pytorch_lightning

In [2]:
# from google.colab import files
# uploaded = files.upload()

In [3]:
import numpy as np
import pandas as pd
import torch
import pytorch_lightning as pl

In [4]:
# データの読み込み（df: data frame）
df = pd.read_csv('wine_class.csv')

In [5]:
# データの表示（先頭の5件）
df.head()

Class  Alcohol   Ash  Alcalinity of ash  Magnesium  Total phenols  \
0      1    14.23  2.43               15.6        127           2.80   
1      1    13.20  2.14               11.2        100           2.65   
2      1    13.16  2.67               18.6        101           2.80   
3      1    14.37  2.50               16.8        113           3.85   
4      1    13.24  2.87               21.0        118           2.80   

   Flavanoids  Nonflavanoid phenols  Color intensity   Hue  Proline  
0        3.06                  0.28             5.64  1.04     1065  
1        2.76                  0.26             4.38  1.05     1050  
2        3.24                  0.30             5.68  1.03     1185  
3        3.49                  0.24             7.80  0.86     1480  
4        2.69                  0.39             4.32  1.04      735

In [6]:
np.unique(df['Class'], return_counts=True)

(array([1, 2, 3]), array([59, 71, 48]))

In [7]:
x = df.drop('Class', axis=1)
t = df['Class']

In [8]:
# Tensor 形式へ変換
x = torch.tensor(x.values, dtype=torch.float32)
t = torch.tensor(t.values, dtype=torch.int64)

In [9]:
# ラベルを 0 から始める
t = t - 1 
t

tensor([0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
        1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 2, 2, 2, 2])

In [10]:
import torch.utils.data

In [11]:
# 入力変数と目的変数をまとめて、ひとつのオブジェクト dataset に変換
dataset = torch.utils.data.TensorDataset(x, t)
dataset

In [12]:
# 各データセットのサンプル数を決定
# train : val : test = 60% : 20% : 20%
n_train = int(len(dataset) * 0.6)
n_val = int((len(dataset) - n_train) * 0.5)
n_test = len(dataset) - n_train - n_val

In [13]:
# サンプル数の確認
n_train, n_val, n_test

(106, 36, 36)

In [14]:
# ランダムに分割を行うため、シードを固定して再現性を確保
torch.manual_seed(0)

# データセットの分割
train, val, test = torch.utils.data.random_split(dataset, [n_train, n_val, n_test])

In [15]:
import torch.nn as nn
import torch.nn.functional as F

In [16]:
class Net(pl.LightningModule):
    
    # バッチサイズ等を引数に指定
    def __init__(self, input_size=10, hidden_size=5, output_size=3, batch_size=10):
        super(Net, self).__init__()
        self.fc1 = nn.Linear(input_size, hidden_size)
        self.fc2 = nn.Linear(hidden_size, output_size)
        self.batch_size = batch_size
    
    # 変更なし
    def forward(self, x):
        x = self.fc1(x)
        x = F.relu(x)
        x = self.fc2(x)
        return x
    
    # 目的関数の設定
    def lossfun(self, y, t):
        return F.cross_entropy(y, t)
    
    # optimizer の設定
    def configure_optimizers(self):
        return torch.optim.SGD(self.parameters(), lr=0.1)
    
    # train 用の DataLoader の設定
    @pl.data_loader
    def train_dataloader(self):
        return torch.utils.data.DataLoader(train, self.batch_size, shuffle=True)
    
    # 学習データに対する処理
    def training_step(self, batch, batch_nb):
        x, t = batch
        y = self.forward(x)
        loss = self.lossfun(y, t)
        results = {'loss': loss}
        return results
    
    # 検証用データセットの設定
    @pl.data_loader
    def val_dataloader(self):
        return torch.utils.data.DataLoader(val, self.batch_size)
    
    # 検証データに対するイテレーションごとの処理
    def validation_step(self, batch, batch_nb):
        x, t = batch
        y = self.forward(x)
        loss = self.lossfun(y, t)
        
        # 正解率の算出
        y_label = torch.argmax(y, dim=1)
        acc = torch.sum(t == y_label) * 1.0 / len(t)
        results = {'val_loss': loss, 'val_acc': acc}
        return results
    
    # 検証データに対するエポックごとの処理
    def validation_end(self, outputs):
        # 各イテレーションごとに得られた値をまとめて、平均値の取得
        avg_loss = torch.stack([x['val_loss'] for x in outputs]).mean()
        avg_acc  =torch.stack([x['val_acc'] for x in outputs]).mean()
        results = {'val_loss': avg_loss, 'val_acc': avg_acc}
        return results
    
    # テストデータセットの設定
    @pl.data_loader
    def test_dataloader(self):
        return torch.utils.data.DataLoader(test, self.batch_size)
    
    # テストデータに対するイテレーションごとの処理
    def test_step(self, batch, batch_nb):
        x, t = batch
        y = self.forward(x)
        loss = self.lossfun(y, t)
        y_label = torch.argmax(y, dim=1)
        acc = torch.sum(t == y_label) * 1.0 / len(t)
        results = {'test_loss': loss, 'test_acc': acc}
        return results
    
    # テストデータに対するエポックごとの処理
    def test_end(self, outputs):
        avg_loss = torch.stack([x['test_loss'] for x in outputs]).mean()
        avg_acc = torch.stack([x['test_acc'] for x in outputs]).mean()
        results = {'test_loss': avg_loss, 'test_acc': avg_acc}
        return results

In [17]:
# モデルの学習
from pytorch_lightning import Trainer

In [18]:
# 乱数のシード固定
torch.manual_seed(0)

# インスタンス化
net = Net()

In [19]:
# 学習用に用いるクラスの Trainer をインスタンス化
trainer = Trainer()

GPU available: False, used: False
TPU available: False, using: 0 TPU cores


In [20]:
# Trainer によるモデルの学習
trainer.fit(net)

/Users/yutaro/miniconda3/lib/python3.7/site-packages/pytorch_lightning/utilities/distributed.py:25: RuntimeWarning: You have defined a `val_dataloader()` and have defined a `validation_step()`, you may also want to define `validation_epoch_end()` for accumulating stats.
  warnings.warn(*args, **kwargs)
/Users/yutaro/miniconda3/lib/python3.7/site-packages/pytorch_lightning/utilities/distributed.py:25: RuntimeWarning: You have defined a `test_dataloader()` and have defined a `test_step()`, you may also want to define `test_epoch_end()` for accumulating stats.
  warnings.warn(*args, **kwargs)

  | Name | Type   | Params
--------------------------------
0 | fc1  | Linear | 55    
1 | fc2  | Linear | 18    
/Users/yutaro/miniconda3/lib/python3.7/site-packages/pytorch_lightning/utilities/distributed.py:25: UserWarning: The dataloader, val dataloader 0, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 8 which is the number

/Users/yutaro/miniconda3/lib/python3.7/site-packages/pytorch_lightning/utilities/distributed.py:25: UserWarning: The dataloader, train dataloader, does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` (try 8 which is the number of cpus on this machine) in the `DataLoader` init to improve performance.
  warnings.warn(*args, **kwargs)


1

In [21]:
# テストデータに対する処理の実行（test_step と test_end）
trainer.test()

TypeError: new(): argument 'size' must be tuple of ints, but found element of type dict at pos 2

In [22]:
#  テストデータに対する結果の確認
trainer.callback_metrics

{'loss': tensor(1.0431),
 'val_loss': tensor(1.0852),
 'val_acc': tensor(0.3917),
 'epoch': 1000}

In [23]:
# 学習データに対する処理
class TrainNet(pl.LightningModule):

    @pl.data_loader
    def train_dataloader(self):
        return torch.utils.data.DataLoader(train, self.batch_size, shuffle=True)

    def training_step(self, batch, batch_nb):
        x, t = batch
        y = self.forward(x)
        loss = self.lossfun(y, t)
        results = {'loss': loss}
        return results

In [24]:
# 検証データに対する処理
class ValidationNet(pl.LightningModule):

    @pl.data_loader
    def val_dataloader(self):
        return torch.utils.data.DataLoader(val, self.batch_size)

    def validation_step(self, batch, batch_nb):
        x, t = batch
        y = self.forward(x)
        loss = self.lossfun(y, t)
        y_label = torch.argmax(y, dim=1)
        acc = torch.sum(t == y_label) * 1.0 / len(t)
        results = {'val_loss': loss, 'val_acc': acc}
        return results

    def validation_end(self, outputs):
        avg_loss = torch.stack([x['val_loss'] for x in outputs]).mean()
        avg_acc = torch.stack([x['val_acc'] for x in outputs]).mean()
        results = {'val_loss': avg_loss, 'val_acc': avg_acc}
        return results

In [25]:
# テストデータに対する処理
class TestNet(pl.LightningModule):

    @pl.data_loader
    def test_dataloader(self):
        return torch.utils.data.DataLoader(test, self.batch_size)

    def test_step(self, batch, batch_nb):
        x, t = batch
        y = self.forward(x)
        loss = self.lossfun(y, t)
        y_label = torch.argmax(y, dim=1)
        acc = torch.sum(t == y_label) * 1.0 / len(t)
        results = {'test_loss': loss, 'test_acc': acc}
        return results

    def test_end(self, outputs):
        avg_loss = torch.stack([x['test_loss'] for x in outputs]).mean()
        avg_acc = torch.stack([x['test_acc'] for x in outputs]).mean()
        results = {'test_loss': avg_loss, 'test_acc': avg_acc}
        return results

In [26]:
# 学習データ、検証データ、テストデータへの処理を継承したクラス
class Net(TrainNet, ValidationNet, TestNet):
    
    def __init__(self, input_size=10, hidden_size=5, output_size=3, batch_size=10):
        super(Net, self).__init__()
        self.fc1 = nn.Linear(input_size, hidden_size)
        self.fc2 = nn.Linear(hidden_size, output_size)
        self.batch_size = batch_size

    def forward(self, x):
        x = self.fc1(x)
        x = F.relu(x)
        x = self.fc2(x)
        return x

    def lossfun(self, y, t):
        return F.cross_entropy(y, t)

    def configure_optimizers(self):
        return torch.optim.SGD(self.parameters(), lr=0.1)

In [27]:
# 学習に関する一連の流れを実行
torch.manual_seed(0)

net = Net()
trainer = Trainer()

trainer.fit(net)

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
/Users/yutaro/miniconda3/lib/python3.7/site-packages/pytorch_lightning/utilities/distributed.py:25: RuntimeWarning: You have defined a `val_dataloader()` and have defined a `validation_step()`, you may also want to define `validation_epoch_end()` for accumulating stats.
  warnings.warn(*args, **kwargs)
/Users/yutaro/miniconda3/lib/python3.7/site-packages/pytorch_lightning/utilities/distributed.py:25: RuntimeWarning: You have defined a `test_dataloader()` and have defined a `test_step()`, you may also want to define `test_epoch_end()` for accumulating stats.
  warnings.warn(*args, **kwargs)

  | Name | Type   | Params
--------------------------------
0 | fc1  | Linear | 55    
1 | fc2  | Linear | 18    


1

In [29]:
# 学習データ、検証データ、テストデータへの処理を継承したクラス
# バッチノーマリゼーション (Batch Normalization)
class Net(TrainNet, ValidationNet, TestNet):
    
    def __init__(self, input_size=10, hidden_size=5, output_size=3, batch_size=10):
        super(Net, self).__init__()
        self.fc1 = nn.Linear(input_size, hidden_size)
        self.fc2 = nn.Linear(hidden_size, output_size)
        self.batch_size = batch_size
        # 追加
        self.bn = nn.BatchNorm1d(input_size)

    def forward(self, x):
        # 追加
        x = self.bn(x)
        x = self.fc1(x)
        x = F.relu(x)
        x = self.fc2(x)
        return x

    def lossfun(self, y, t):
        return F.cross_entropy(y, t)

    def configure_optimizers(self):
        return torch.optim.SGD(self.parameters(), lr=0.1)

In [30]:
# 学習に関する一連の流れを実行
torch.manual_seed(0)

net = Net()
trainer = Trainer()

trainer.fit(net)

GPU available: False, used: False
TPU available: False, using: 0 TPU cores

  | Name | Type        | Params
-------------------------------------
0 | fc1  | Linear      | 55    
1 | fc2  | Linear      | 18    
2 | bn   | BatchNorm1d | 20    


1

In [31]:
# テストデータに対する処理の実行（test_step と test_end）
trainer.test()

TypeError: new(): argument 'size' must be tuple of ints, but found element of type dict at pos 2

In [32]:
# 結果の確認
trainer.callback_metrics

{'loss': tensor(0.3642),
 'val_loss': tensor(0.1714),
 'val_acc': tensor(0.9583),
 'epoch': 1000}

In [33]:
# モデルの重み
net.state_dict()

OrderedDict([('fc1.weight',
              tensor([[-0.6395, -0.0675,  0.9102, -1.2847, -0.7223,  1.5203,  0.6327,  0.5376,
                        0.2578, -1.5403],
                      [-0.9007, -0.7294, -0.2344,  1.1583,  1.1011, -1.3186, -0.7592,  0.0174,
                        1.4096, -0.2328],
                      [-1.2182,  0.0486,  0.4524,  0.0831,  0.1028, -0.1950, -0.2543,  0.0065,
                       -0.6517,  0.6191],
                      [-0.1652,  0.6395,  0.2109,  0.1151,  0.8275, -1.5212, -0.4516,  1.3918,
                        0.0488, -0.3750],
                      [ 0.6064, -0.5856,  0.0500,  0.1909, -0.0860, -1.0338,  0.0880, -0.0812,
                        0.1509, -0.3028]])),
             ('fc1.bias', tensor([0.2630, 0.5170, 0.1636, 0.3135, 0.8004])),
             ('fc2.weight',
              tensor([[-1.0781,  0.0720, -1.4104, -0.3151, -1.6638],
                      [ 0.9968,  1.1053,  0.4152, -0.5122,  1.0876],
                      [-0.0361, -0.8971, 

In [34]:
# 学習済みモデルを保存
torch.save(net.state_dict(), 'wine.pt')